# प्रोडक्शन में AutoGen एजेंट्स: निगरानी और मूल्यांकन

इस ट्यूटोरियल में, हम सीखेंगे कि **[Autogen एजेंट्स](https://github.com/microsoft/autogen)** के आंतरिक चरणों (ट्रेस) की निगरानी कैसे करें और [Langfuse](https://langfuse.com) का उपयोग करके **इसके प्रदर्शन का मूल्यांकन** कैसे करें।

यह गाइड **ऑनलाइन** और **ऑफलाइन** मूल्यांकन मेट्रिक्स को कवर करता है, जिनका उपयोग टीमों द्वारा एजेंट्स को तेज़ और विश्वसनीय तरीके से प्रोडक्शन में लाने के लिए किया जाता है।

**AI एजेंट मूल्यांकन क्यों महत्वपूर्ण है:**
- जब कार्य विफल होते हैं या उपयुक्त परिणाम नहीं देते हैं, तो समस्याओं का डिबग करना
- वास्तविक समय में लागत और प्रदर्शन की निगरानी करना
- निरंतर फीडबैक के माध्यम से विश्वसनीयता और सुरक्षा में सुधार करना


## चरण 1: पर्यावरण वेरिएबल्स सेट करें

[Langfuse Cloud](https://cloud.langfuse.com/) के लिए साइन अप करके या [Langfuse को स्वयं होस्ट करें](https://langfuse.com/self-hosting) के माध्यम से अपने Langfuse API कुंजियाँ प्राप्त करें।

_**नोट:** स्वयं होस्ट करने वाले उपयोगकर्ता [Terraform modules](https://langfuse.com/self-hosting/azure) का उपयोग करके Azure पर Langfuse को डिप्लॉय कर सकते हैं। वैकल्पिक रूप से, आप [Helm chart](https://langfuse.com/self-hosting/kubernetes-helm) का उपयोग करके Kubernetes पर Langfuse को डिप्लॉय कर सकते हैं।_


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

पर्यावरण चर सेट होने के साथ, अब हम Langfuse क्लाइंट को प्रारंभ कर सकते हैं। `get_client()` पर्यावरण चर में प्रदान की गई प्रमाण-पत्रों का उपयोग करके Langfuse क्लाइंट को प्रारंभ करता है।


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## चरण 2: OpenLit इंस्ट्रुमेंटेशन प्रारंभ करें

अब, हम [OpenLit](https://github.com/openlit/openlit) इंस्ट्रुमेंटेशन को प्रारंभ करते हैं। OpenLit स्वचालित रूप से AutoGen ऑपरेशन्स को कैप्चर करता है और OpenTelemetry (OTel) स्पैन्स को Langfuse में एक्सपोर्ट करता है।


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## चरण 3: अपने एजेंट को चलाएं

अब हम अपने इंस्ट्रूमेंटेशन का परीक्षण करने के लिए एक मल्टी-टर्न एजेंट सेट अप करते हैं।


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### ट्रेस संरचना

Langfuse एक **ट्रेस** रिकॉर्ड करता है जिसमें **स्पैन** शामिल होते हैं, जो आपके एजेंट की लॉजिक के प्रत्येक चरण का प्रतिनिधित्व करते हैं। यहां, ट्रेस में समग्र एजेंट रन और निम्नलिखित के लिए सब-स्पैन शामिल हैं:
- मील प्लानर एजेंट
- न्यूट्रिशनिस्ट एजेंट

आप इनका निरीक्षण कर सकते हैं यह देखने के लिए कि समय कहां खर्च हो रहा है, कितने टोकन उपयोग हो रहे हैं, और अन्य विवरण:

![Langfuse में ट्रेस ट्री](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[ट्रेस का लिंक](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## ऑनलाइन मूल्यांकन

ऑनलाइन मूल्यांकन का मतलब है एजेंट का मूल्यांकन एक लाइव, वास्तविक दुनिया के वातावरण में करना, यानी प्रोडक्शन में वास्तविक उपयोग के दौरान। इसमें एजेंट के प्रदर्शन की निगरानी करना और वास्तविक उपयोगकर्ता इंटरैक्शन पर लगातार परिणामों का विश्लेषण करना शामिल है।

### प्रोडक्शन में ट्रैक करने के लिए सामान्य मेट्रिक्स

1. **लागत** — इंस्ट्रूमेंटेशन टोकन उपयोग को कैप्चर करता है, जिसे आप प्रति टोकन कीमत निर्धारित करके अनुमानित लागत में बदल सकते हैं।
2. **लेटेंसी** — प्रत्येक चरण को पूरा करने या पूरे रन में लगने वाले समय का अवलोकन करें।
3. **उपयोगकर्ता प्रतिक्रिया** — उपयोगकर्ता सीधे फीडबैक (थंब्स अप/डाउन) देकर एजेंट को सुधारने या सही करने में मदद कर सकते हैं।
4. **LLM-एज़-अ-जज** — आपके एजेंट के आउटपुट का लगभग वास्तविक समय में मूल्यांकन करने के लिए एक अलग LLM का उपयोग करें (जैसे, विषाक्तता या शुद्धता की जांच करना)।

नीचे, हम इन मेट्रिक्स के उदाहरण दिखाते हैं।


#### 1. लागत

नीचे `gpt-4o-mini` कॉल्स के उपयोग को दिखाने वाला एक स्क्रीनशॉट है। यह महंगे चरणों को देखने और आपके एजेंट को अनुकूलित करने में सहायक है।

![Costs](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[ट्रेस के लिए लिंक](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. विलंबता

हम यह भी देख सकते हैं कि प्रत्येक चरण को पूरा करने में कितना समय लगा। नीचे दिए गए उदाहरण में, पूरे रन को लगभग 3 सेकंड लगे, जिसे आप चरणों के अनुसार विभाजित कर सकते हैं। यह आपको बाधाओं की पहचान करने और अपने एजेंट को अनुकूलित करने में मदद करता है।

![विलंबता](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[ट्रेस का लिंक](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. उपयोगकर्ता प्रतिक्रिया

यदि आपका एजेंट किसी उपयोगकर्ता इंटरफ़ेस में एम्बेड किया गया है, तो आप सीधे उपयोगकर्ता प्रतिक्रिया रिकॉर्ड कर सकते हैं (जैसे चैट UI में थम्स-अप/डाउन)।


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

उपयोगकर्ता की प्रतिक्रिया फिर Langfuse में कैप्चर की जाती है:

![उपयोगकर्ता की प्रतिक्रिया Langfuse में कैप्चर की जा रही है](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. स्वचालित LLM-as-a-Judge स्कोरिंग

LLM-as-a-Judge आपके एजेंट के आउटपुट का स्वचालित रूप से मूल्यांकन करने का एक और तरीका है। आप आउटपुट की शुद्धता, विषाक्तता, शैली, या किसी अन्य मानदंड को जांचने के लिए एक अलग LLM कॉल सेट कर सकते हैं।

**कार्यप्रवाह**:
1. आप एक **मूल्यांकन टेम्पलेट** परिभाषित करते हैं, जैसे "जांचें कि क्या टेक्स्ट विषाक्त है।"
2. आप एक मॉडल सेट करते हैं जिसे जज-मॉडल के रूप में उपयोग किया जाता है; इस मामले में `gpt-4o-mini` जिसे Azure के माध्यम से क्वेरी किया जाता है।
2. हर बार जब आपका एजेंट आउटपुट उत्पन्न करता है, तो आप उस आउटपुट को टेम्पलेट के साथ "जज" LLM को पास करते हैं।
3. जज LLM एक रेटिंग या लेबल के साथ प्रतिक्रिया देता है जिसे आप अपने ऑब्ज़र्वेबिलिटी टूल में लॉग करते हैं।

Langfuse से उदाहरण:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

आप देख सकते हैं कि इस उदाहरण का उत्तर "अवांछनीय" नहीं माना गया है।

![LLM-as-a-Judge मूल्यांकन स्कोर](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. अवलोकनीयता मेट्रिक्स का अवलोकन

इन सभी मेट्रिक्स को डैशबोर्ड में एक साथ देखा जा सकता है। यह आपको यह जल्दी से समझने में मदद करता है कि आपका एजेंट कई सत्रों में कैसा प्रदर्शन कर रहा है और समय के साथ गुणवत्ता मेट्रिक्स को ट्रैक करने में सहायता करता है।

![अवलोकनीयता मेट्रिक्स का अवलोकन](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## ऑफलाइन मूल्यांकन

ऑनलाइन मूल्यांकन लाइव फीडबैक के लिए महत्वपूर्ण है, लेकिन आपको **ऑफलाइन मूल्यांकन** की भी आवश्यकता होती है—विकास से पहले या उसके दौरान व्यवस्थित जांच। यह उत्पादन में बदलाव लागू करने से पहले गुणवत्ता और विश्वसनीयता बनाए रखने में मदद करता है।


### डेटासेट मूल्यांकन

ऑफ़लाइन मूल्यांकन में, आप आमतौर पर:
1. एक बेंचमार्क डेटासेट रखते हैं (जिसमें प्रॉम्प्ट और अपेक्षित आउटपुट के जोड़े होते हैं)
2. अपने एजेंट को उस डेटासेट पर चलाते हैं
3. आउटपुट की तुलना अपेक्षित परिणामों से करते हैं या अतिरिक्त स्कोरिंग तंत्र का उपयोग करते हैं

नीचे, हम इस दृष्टिकोण को [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset) के साथ प्रदर्शित करते हैं, जिसमें प्रश्न और अपेक्षित उत्तर शामिल हैं।


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

इसके बाद, हम रन को ट्रैक करने के लिए Langfuse में एक डेटासेट इकाई बनाते हैं। फिर, हम डेटासेट से प्रत्येक आइटम को सिस्टम में जोड़ते हैं।


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![डेटासेट आइटम्स इन लैंगफ्यूज](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### डेटासेट पर एजेंट चलाना

सबसे पहले, हम एक साधारण Autogen एजेंट तैयार करते हैं जो Azure OpenAI मॉडल का उपयोग करके सवालों के जवाब देता है।


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

फिर, हम एक सहायक फ़ंक्शन `my_agent()` परिभाषित करते हैं।


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

अंत में, हम प्रत्येक डेटासेट आइटम पर लूप करते हैं, एजेंट को चलाते हैं, और ट्रेस को डेटासेट आइटम से जोड़ते हैं। यदि चाहें तो हम एक त्वरित मूल्यांकन स्कोर भी जोड़ सकते हैं।


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

महत्वपूर्ण नियम:  
1. इस प्रक्रिया में विभिन्न एजेंट कॉन्फ़िगरेशन का उपयोग किया जा सकता है, जैसे:  
   - मॉडल्स (जैसे gpt-4o-mini, gpt-4.1, आदि)  
   - प्रॉम्प्ट्स  
   - टूल्स (सर्च बनाम बिना सर्च)  
   - एजेंट की जटिलता (मल्टी एजेंट बनाम सिंगल एजेंट)  

2. फिर आप उन्हें Langfuse में साइड-बाय-साइड तुलना कर सकते हैं। इस उदाहरण में, मैंने एजेंट को 25 डेटासेट प्रश्नों पर 3 बार चलाया। प्रत्येक रन के लिए, मैंने एक अलग Azure OpenAI मॉडल का उपयोग किया। आप देख सकते हैं कि बड़े मॉडल का उपयोग करने पर सही उत्तरों की संख्या में सुधार होता है (जैसा कि अपेक्षित था)।  

3. `correct_answer` स्कोर एक [LLM-as-a-Judge Evaluator](https://langfuse.com/docs/scores/model-based-evals) द्वारा बनाया गया है, जिसे डेटासेट में दिए गए नमूना उत्तर के आधार पर प्रश्न की शुद्धता का मूल्यांकन करने के लिए सेट किया गया है।  

![डेटासेट रन का अवलोकन](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)  
![डेटासेट रन तुलना](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)  



---

**अस्वीकरण**:  
यह दस्तावेज़ AI अनुवाद सेवा [Co-op Translator](https://github.com/Azure/co-op-translator) का उपयोग करके अनुवादित किया गया है। जबकि हम सटीकता के लिए प्रयासरत हैं, कृपया ध्यान दें कि स्वचालित अनुवाद में त्रुटियां या अशुद्धियां हो सकती हैं। मूल भाषा में उपलब्ध मूल दस्तावेज़ को आधिकारिक स्रोत माना जाना चाहिए। महत्वपूर्ण जानकारी के लिए, पेशेवर मानव अनुवाद की सिफारिश की जाती है। इस अनुवाद के उपयोग से उत्पन्न किसी भी गलतफहमी या गलत व्याख्या के लिए हम उत्तरदायी नहीं हैं।  
